In [6]:
import requests
import base64
from bs4 import BeautifulSoup
import time
import threading
import urllib.request 
import webbrowser
import datetime
#File
from datetime import datetime, timedelta, timezone
import os
from PIL import ImageTk
import PIL.Image
#UI
from tkinter import *
from tkinter import ttk
import tkinter.messagebox
import tkinter.font
import clipboard

def resource_path(relpath):
    try:
        abspath = sys._MEIPASS
    except Exception:
        abspath = os.path.abspath(".")
    return os.path.join(abspath, relpath)

In [7]:
class HTML():
    headers = {
        "contentType": "application/json",
        "User-Agent" : "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/74.0.3729.169 Safari/537.36"
    }

    params = {
        "type": "legion",
        "page_index": 1,
        "id": 0
    }
    
    def GetHTML(url):
        response = requests.get(url, headers=HTML.headers)
        # ip차단 방지를 위해 일시정지
        #time.sleep(0.9)
        return BeautifulSoup(response.text, "html.parser")
    
    def GetLegionJson(url, server_code, page_index):
        HTML.params["id"] = server_code
        HTML.params["page_index"] = page_index

        response = requests.get(url, headers=HTML.headers, params=HTML.params)
        # ip차단 방지를 위해 일시정지
        #time.sleep(0.9)
        if response.status_code == 200 :
            # print(f"GetLegionJson: {response.json()}")
            return response.json()
        else :
            # print(f"GetLegionJson status not 200 : {response.status_code}")
            return None
    
    def GetUnionTop(html):
        return html["ranks"][0]["legionLevel"]


    def GetUnionBottom(html):
        return html["ranks"][len(html["ranks"])-1]["legionLevel"]
        
    def GetCharacterInfoAll(html):
        # 모든 캐릭터 정보를 저장할 리스트 선언
        data_tuple_list = []

        # 모든 캐릭터 정보 추출
        for character_info in html["ranks"]:
            nick = character_info["characterName"]
            job = Crawlling.GetJobStr(character_info["jobID"], character_info["jobDetail"])
            union = character_info["legionLevel"]
            img_url = character_info["characterImgURL"]
            level = character_info["level"]
            data_tuple_list.append((nick, job, union, img_url, level))

        return data_tuple_list
    

In [8]:
class Crawlling(HTML):
    is_running = False
    url = None
    search_min = 1
    search_max = 1
    server_code = 0
    char_count = 0
    char_list = []
    
    def TempCode_InputInfo():
        GUI.server_combobox.set("크로아")
        GUI.union_min_entry.delete(0, len(GUI.union_min_entry.get()))
        GUI.union_max_entry.delete(0, len(GUI.union_max_entry.get()))
        GUI.union_min_entry.insert(0, '9055')
        GUI.union_max_entry.insert(0, '9055')
        
    def DeActivateReservation():
        Crawlling.is_running = False
        GUI.activate_button.config(text = "Start")
        GUI.SetProgressLabelMessage('')
        GUI.EnableUi()

    def GetTime_Thread():
        while(True):
            GUI.SetRemainResetTime()
            time.sleep(1)

    def GetJobStr(jobID, jobDetail):
        #                               jobID   JobDetail
        #                   Explorer
        #   Beginner                      0         0
        #                   Warrior
        #   Hero                          1         12
        #   Paladin                       1         22
        #   Dark Knight                   1         32
        #                   Magician
        #   Magician (Fire, Poison)       2         12
        #   Magician (Ice, Lightning)     2         22
        #   Bishop                        2         32
        #                   Bowman
        #   Bowmaster                     3         12
        #   Marksman                      3         22
        #   Pathfinder                    3         32
        #                   Thief
        #   Night Lord                    4         12
        #   Shadower                      4         22
        #   Dual Blade                    4         34
        #                   Pirate
        #   Buccaneer                     5         12
        #   Corsair                       5         22
        #   Cannoneer                     5         32
        #                   Cygnus Knights
        #   Noblesse                      10        0
        #   Dawn Warrior                  11        12
        #   Blaze Wizard                  12        12
        #   Wind Archer                   13        12
        #   Night Walker                  14        12
        #   Thunder Breaker               15        12
        #   Mihile                        202(51)   12
        #                   Resistance
        #   Citizen                       30        0
        #   Demon Slayer                  31        12
        #   Battle Mage                   32        12
        #   Wild Hunter                   33        12
        #   Mechanic                      35        12
        #   Xenon                         208(36)   12
        #   Demon Avenger                 209(31)   22
        #   Blaster                       215(37)   12
        #                   Hero
        #   Aran                          21        12
        #   Evan                          22        17
        #   Mercedes                      23        12
        #   Phantom                       24        12
        #   Luminous                      203(27)   12
        #   Shade                         212(25)   12
        #                   Nova
        #   Kaiser                        204(61)   12
        #   Angelic Buster                205(65)   12
        #   Cadena                        216(64)   12
        #   Kain                          222(63)   12
        #                   Flora
        #   Illium                        217(152)  12
        #   Ark                           218(155)  12
        #   Adele                         221(151)  12
        #   Khali                         224(154)  12
        #                   Sengoku
        #   Hayato                        206(41)   12
        #   Kanna                         207(42)   12
        #                   Anima
        #   Lara                          223(162)  12
        #   Hoyoung                       220(164)  12
        #                   Others
        #   Zero                          210(101)  12
        #   Kinesis                       214(142)  12
        #   Lynn                          225(172)  12
        job = {
            0: {
                0: 'Beginner'
            },
            1: {
                12: 'Hero',
                22: 'Paladin',
                32: 'Dark Knight',
                0: 'Warrior'
            },
            2: {
                12: 'Magician (Fire, Poison)',
                22: 'Magician (Ice, Lightning)',
                32: 'Bishop',
                0: 'Magician'
            },
            3: {
                12: 'Bowmaster',
                22: 'Marksman',
                32: 'Pathfinder',
                0: 'Bowman'
            },
            4: {
                12: 'Night Lord',
                22: 'Shadower',
                34: 'Dual Blade',
                0: 'Thief'
            },
            5: {
                12: 'Buccaneer',
                22: 'Corsair',
                32: 'Cannoneer',
                0: 'Pirate'
            },
            10: 'Noblesse',
            11: 'Dawn Warrior',
            12: 'Blaze Wizard',
            13: 'Wind Archer',
            14: 'Night Walker',
            15: 'Thunder Breaker',
            202: 'Mihile',
            21: 'Aran',
            22: 'Evan',
            23: 'Mercedes',
            24: 'Phantom',
            203: 'Luminous',
            212: 'Shade',
            30: 'Citizen',
            31: 'Demon Slayer',
            32: 'Battle Mage',
            33: 'Wild Hunter',
            35: 'Mechanic',
            208: 'Xenon',
            209: 'Demon Avenger',
            215: 'Blaster',
            204: 'Kaiser',
            205: 'Angelic Buster',
            216: 'Cadena',
            222: 'Kain',
            217: 'Illium',
            218: 'Ark',
            221: 'Adele',
            224: 'Khali',
            206: 'Hayato',
            207: 'Kanna',
            223: 'Lara',
            220: 'Hoyoung',
            210: 'Zero',
            214: 'Kinesis',
            225: 'Lynn'
        }

        jobIDSearch = job.get(jobID, f"Not Defined JobID : {jobID}")
        if type(jobIDSearch) is dict:
            jobDetailSearch = jobIDSearch.get(jobDetail, f"{jobIDSearch[0]}({jobDetail})")
            return jobDetailSearch
        else:
            return jobIDSearch

    
    def ValidateCrawlling_Thread():
        t1=threading.Thread(target=Crawlling.ValidateCrawlling)
        t1.setDaemon(True)
        t1.deamon = True
        t1.start()

    def ValidateCrawlling():
        # 테스트용 자동 입력
#         Crawlling.TempCode_InputInfo()

        if Crawlling.is_running == True:
            Crawlling.DeActivateReservation()

            if Crawlling.char_count == 0 :
                tkinter.messagebox.showinfo("Message", "Stop the operation at the request of the user.")
            else :
                if tkinter.messagebox.askquestion ('Message','Stop the operation at the request of the user. \nDo you want to save the results so far?') == 'yes':
                    CsvFile.SaveCsvFile()
                return
        else:
            GUI.activate_button.config(text = "Stop")
            Crawlling.is_running = True
        
        # 입력 오류 체크
        if Crawlling.IsExistInputError():
            Crawlling.DeActivateReservation()
            return
        
        # Ui 비활성화 및 CSV 초기화
        GUI.DisableUi()
        CsvFile.ClearCsvText()
        
        # 서버에 따른 URL 설정
        Crawlling.SetURL()
        
        # 탐색 범위 설정(1000단위, 100단위, 10단위로)
        Crawlling.SetSearchRange(1, 100000, 1000)
        Crawlling.SetSearchRange(Crawlling.search_min, Crawlling.search_max+100, 100)
        Crawlling.SetSearchRange(Crawlling.search_min, Crawlling.search_max+10, 10)
        if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
        GUI.SetProgressLabelMessage(f"Finished setting search scope. [{Crawlling.search_min} - {Crawlling.search_max}]")

        # print(f"최종 범위 : {Crawlling.search_min} ~ {Crawlling.search_max}")
        
        # 조건에 맞는 캐릭터 탐색
        Crawlling.FindSuspect()
        if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
        
        if Crawlling.char_count == 0 :
            tkinter.messagebox.showinfo("Result", "No character matches the condition.")
        else :
            # 파일 저장 
            CsvFile.SaveCsvFile()
            if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
            
            # 결과 출력
            Crawlling.ShowResult()
        
        # 작업 종료
        Crawlling.DeActivateReservation()
        
    def IsExistInputError():
        if GUI.server_combobox.get() == '':
            tkinter.messagebox.showerror("Error", "Server is not entered. \nPlease select the correct server.")
            return True
        elif not GUI.union_min_entry.get() or not GUI.union_max_entry.get():
            tkinter.messagebox.showerror("Error", "Legion value is not entered. \nPlease enter legion value.")
            return True
        else:
            try:
                int(GUI.union_min_entry.get())
                int(GUI.union_max_entry.get())
                return False
            except:
                tkinter.messagebox.showerror("Error", "Non-numerical characters were detected in the legion value.")
                return True

    def SetURL():
        server = GUI.GetServer()
        if server ==   'Kronos': server_code = 45; server_region = 'na'
        elif server == 'Hyperion': server_code = 70; server_region = 'na'
        elif server == 'Scania': server_code = 0; server_region = 'na'
        elif server == 'Bera': server_code = 1; server_region = 'na'
        elif server == 'Aurora': server_code = 17; server_region = 'na'
        elif server == 'Elysium': server_code = 18; server_region = 'na'
        elif server == 'Solis': server_code = 46; server_region = 'eu'
        elif server == 'Luna': server_code = 30; server_region = 'eu'
        Crawlling.url = f"https://www.nexon.com/api/maplestory/no-auth/ranking/v2/{server_region}"
        Crawlling.server_code = server_code
        
    def SetSearchRange(start, end, increase):
        if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
        union_range_min = int(GUI.GetUnionMin())
        union_range_max = int(GUI.GetUnionMax())

        # 검색 범위 설정
        for i in range(start, end, increase):
            html = Crawlling.GetLegionJson(f"{Crawlling.url}", Crawlling.server_code, i)
            resErrCnt = 0
            while html is None:
                if resErrCnt >= 5:
                    GUI.SetProgressLabelMessage(f"Maybe Your IP has banned... wait 1m [{i} - {Crawlling.search_max+increase}]", "Red")
                    time.sleep(60)
                    resErrCnt = 0
                else:
                    resErrCnt += 1
                    GUI.SetProgressLabelMessage(f"Server reponse error... wait 3s (count:{resErrCnt}) [{i} - {Crawlling.search_max+increase}]", "Red")
                    time.sleep(3)
                html = Crawlling.GetLegionJson(f"{Crawlling.url}", Crawlling.server_code, i)
                if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
            union_top = int(Crawlling.GetUnionTop(html))
            union_bottom = int(Crawlling.GetUnionBottom(html))
            if union_top == None or union_bottom == None:
                Crawlling.search_max = i
                break
            if union_top > union_range_max:
                Crawlling.search_min = i
            if union_bottom < union_range_min:
                Crawlling.search_max = i
                break
            GUI.SetProgressLabelMessage(f"Setting up a character search range... [{i} - {Crawlling.search_max+increase}]")
            if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
        # print(f"현재 범위 : {Crawlling.search_min} ~ {Crawlling.search_max}")
        
    def FindSuspect():
        Crawlling.char_count = 0
        union_range_min = int(GUI.GetUnionMin())
        union_range_max = int(GUI.GetUnionMax())
        Crawlling.char_list = []
        
        for i in range(Crawlling.search_min, Crawlling.search_max+1, 10):
            html = Crawlling.GetLegionJson(f"{Crawlling.url}", Crawlling.server_code, i)
            resErrCnt = 0
            while html is None:
                if resErrCnt >= 5:
                    GUI.SetProgressLabelMessage(f"Maybe Your IP has banned... wait 1m [{i} - {Crawlling.search_max}]", "Red")
                    time.sleep(60)
                    resErrCnt = 0
                else:
                    resErrCnt += 1
                    GUI.SetProgressLabelMessage(f"Server reponse error... wait 3s (count:{resErrCnt}) [{i} - {Crawlling.search_max}]", "Red")
                    time.sleep(3)
                html = Crawlling.GetLegionJson(f"{Crawlling.url}", Crawlling.server_code, i)
                if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
            
            data_tuple_list = Crawlling.GetCharacterInfoAll(html)

            # print(f"검색결과 : {data_tuple_list}")
            
            # 조건 일치 시 CsvFile 텍스트 내 저장 
            for data_tuple in data_tuple_list:
                character_union = int(data_tuple[2])
                if character_union >= union_range_min and character_union <= union_range_max:
                    Crawlling.char_count += 1
                    nick = data_tuple[0]
                    job = data_tuple[1]
                    img_url = data_tuple[3]
                    level = data_tuple[4]
                    CsvFile.AppendCsvText(f"{nick},\"{job}\",{character_union},{level},{img_url}")
                    # 리스트에 저장
                    Crawlling.char_list.append({
                        "nick": data_tuple[0],
                        "job": data_tuple[1],
                        "union": character_union,
                        "img_url": data_tuple[3],
                        "level": data_tuple[4]
                    })
                if Crawlling.is_running == False : Crawlling.DeActivateReservation(); return 0
                
                # character_union이 최소 조건보다 작으면 탐색 종료
                if character_union < union_range_min:
                    return
                
            GUI.SetProgressLabelMessage(f"Finding a character that fits the conditions... [{i} / {Crawlling.search_max}]")
            

    def ShowResult():
        # 기존 소스 재활용
        # character_info_list = CsvFile.csv_text.split('\n')
        character_info_list = Crawlling.char_list
        # loading_img = ImageTk.PhotoImage(PIL.Image.open("img/loading.gif"))
        # GIF 프레임 로드 (초기화 시 호출)
        gif_path = "img/loading.gif"
        gif_image = PIL.Image.open(gif_path)
        gif_frames = []
        for i in range(gif_image.n_frames):
            gif_image.seek(i)
            frame = gif_image.convert("RGBA")  # 모드 변환
            gif_frames.append(ImageTk.PhotoImage(frame))
        gif_running = False

        def CopyNickname(event):
            nonlocal character_info_list
            broadcast_label.config(text = "Copy completed!", foreground='blue')
            nick = character_info_list[page-1]["nick"]
            clipboard.copy(nick)
            
        def BeforeInfo():
            nonlocal page
            if page <= 1:
                page = page_max
                ShowCharacterInfo()
            else:
                page -= 1
                ShowCharacterInfo()

        def NextInfo():
            nonlocal page
            if page >= page_max:
                page = 1
                ShowCharacterInfo()
            else:
                page += 1
                ShowCharacterInfo()
                
        # def ShowCharacterInfo():
        #     nonlocal character_info_list
        #     nick = character_info_list[page-1].get("nick")
        #     job = character_info_list[page-1].get("job")
        #     union = character_info_list[page-1].get("union")
        #     level = character_info_list[page-1].get("level")
        #     img_url = character_info_list[page-1].get("img_url")
        #     character_img = character_info_list[page-1].get("img")
            
        #     #Get img raw
        #     if not character_img:
        #         character_img_label.config(image = loading_img)
        #         broadcast_label.config(text = 'Loading Character image...\n\nPlease Wait', font = tkinter.font.Font(size = 8))
        #         character_img_label.image = loading_img
        #         nick_label.config(text = '')
        #         job_label.config(text = '')
        #         union_label.config(text = '')
        #         level_label.config(text = '')
        #         # time.sleep(0.00001)
        #         character_img = ImageTk.PhotoImage(PIL.Image.open(requests.get(img_url, stream=True).raw))
        #         character_info_list[page-1]["img"] = character_img
        #     # character_img = ImageTk.PhotoImage(PIL.Image.open(requests.get(img_url, stream=True).raw))
            
        #     #Info to Toplevel
        #     broadcast_label.config(text = "Click on the image to copy the name.", foreground='black')
        #     page_label.config(text = f"[{page} / {page_max}]")
        #     character_img_label.config(image = character_img)
        #     character_img_label.image = character_img # GC 이미지 삭제 방지        
        #     nick_label.config(text = nick)
        #     job_label.config(text = 'Job : '+job)
        #     union_label.config(text = 'Legion : '+str(union))
        #     level_label.config(text = 'Level : '+str(level))

        def ShowCharacterInfo():
            nonlocal character_info_list, gif_running
            nick = character_info_list[page-1].get("nick")
            job = character_info_list[page-1].get("job")
            union = character_info_list[page-1].get("union")
            level = character_info_list[page-1].get("level")
            img_url = character_info_list[page-1].get("img_url")
            character_img = character_info_list[page-1].get("img")

            # 로딩 중 UI 초기화
            def update_gif(frame_index):
                if not gif_running:
                    return
                # 프레임 업데이트
                frame = gif_frames[frame_index]
                character_img_label.config(image=frame)
                character_img_label.image = frame
                # 다음 프레임 설정
                next_frame = (frame_index + 1) % len(gif_frames)
                character_img_label.after(100, update_gif, next_frame)

            # GIF 애니메이션 시작
            gif_running = True
            update_gif(0)
            broadcast_label.config(text='Loading Character image...\n\nPlease Wait', font=tkinter.font.Font(size=8))
            nick_label.config(text='')
            job_label.config(text='')
            union_label.config(text='')
            level_label.config(text='')

            def load_image():
                nonlocal character_img, gif_running
                try:
                    if not character_img:
                        # 이미지 로드
                        character_img = ImageTk.PhotoImage(PIL.Image.open(requests.get(img_url, stream=True).raw))
                        character_info_list[page-1]["img"] = character_img
                    
                    # 이미지 로딩 완료 후 UI 업데이트
                    gif_running = False  # GIF 애니메이션 종료
                    character_img_label.config(image=character_img)
                    character_img_label.image = character_img
                    nick_label.config(text=nick)
                    job_label.config(text='Job : ' + job)
                    union_label.config(text='Legion : ' + str(union))
                    level_label.config(text='Level : ' + str(level))
                    broadcast_label.config(text='Click on the image to copy the name.', foreground='black')
                    page_label.config(text=f"[{page} / {page_max}]")
                except Exception as e:
                    gif_running = False  # GIF 애니메이션 종료
                    broadcast_label.config(text=f"Error loading image: {e}", foreground='red')

            # 이미지 로드 작업을 별도의 스레드에서 실행
            threading.Thread(target=load_image).start()
                
        #Toplevel Ui
        page = 1
        page_max = len(character_info_list)
        result_window = Toplevel()
        result_window.title("Result")
        result_window.iconbitmap(resource_path("img/app.ico"))
        result_window.geometry('230x250')
        # result_window.option_add('*Font', '맑은고딕 9')
        result_window.resizable(False, False)
        character_img_label = Label(result_window)
        character_img_label.bind('<Button-1>', CopyNickname)
        # character_img_label.config(image = loading_img)
        page_label = Label(result_window, font = tkinter.font.Font(size = 8))
        broadcast_label = Label(result_window, text = '', font = tkinter.font.Font(size = 8))
        nick_label = Label(result_window)
        nick_label.bind('<Button-1>', CopyNickname)
        job_label = Label(result_window)
        union_label = Label(result_window)
        level_label = Label(result_window)
        BeforeBtn = Button(result_window, width = 10, text = 'prev', command = BeforeInfo)
        NextBtn = Button(result_window, width = 10, text = 'next', command = NextInfo)
        
        page_label.pack()
        broadcast_label.pack()
        character_img_label.pack()
        nick_label.pack()
        union_label.pack()
        level_label.pack()
        job_label.pack()
        BeforeBtn.place(x = 5, y = 222)
        NextBtn.place(x = 145, y = 222)

        # 캐릭터 이미지 로딩
        # for i in character_info_list:
        #     i["img"] = ImageTk.PhotoImage(PIL.Image.open(requests.get(i["img_url"], stream=True).raw))

        # broadcast_label.config(text = 'Click on the image to copy the name.', font = tkinter.font.Font(size = 8))

        ShowCharacterInfo()

In [9]:
class CsvFile():
    csv_text = "Name,Job,Legion,Level,Img\n"
    
    def ClearCsvText():
        CsvFile.csv_text = "Name,Job,Legion,Level,Img\n"
        
    def AppendCsvText(text):
        # print(f"CSV 저장 : {text}")
        CsvFile.csv_text += f"{text}\n"
        
    def SaveCsvFile():
        GUI.SetProgressLabelMessage("Saving CSV file...")
        file_name = f"[{GUI.GetServer()}] {GUI.GetUnionMin()} - {GUI.GetUnionMax()} Result ({datetime.today().strftime('%d-%m-%Y-%H%M%S')}).csv"
        with open(file_name,'w',encoding='utf-8-sig') as file:
            file.write(CsvFile.csv_text)
        tkinter.messagebox.showinfo("Result", f"{file_name}\n file has been saved.")
        GUI.SetProgressLabelMessage("")

In [10]:
class Update():
    present_version = '1.1.0'
    newest_version = None
    message = None
    update_url = None
    
    def CheckUpdate():
        try:
            url = 'https://blog.naver.com/PostView.naver?blogId=dlgudfo99&Redirect=View&logNo=223785571264&categoryNo=15&isAfterWrite=true&isMrblogPost=false&isHappyBeanLeverage=true&contentLength=4867'
            html = HTML.GetHTML(url)
            Update.newest_version = html.select('div.se-component-content')[1].select('p')[1].text
            Update.message = html.select('div.se-component-content')[1].select('p')[4].text.replace('\\n', '\n')
            Update.update_url = html.select('div.se-component-content')[1].select('p')[7].text

            # print(f"{Update.message}")

            if Update.present_version != Update.newest_version:
                if tkinter.messagebox.askquestion ('Update', f"New version ({Update.newest_version}) detected. \n(Current version : {Update.present_version})\n\nNotice :\n{Update.message} \n\nClick Yes to download.") == 'yes':
                    Update.GoDownloadURL()
        except:
            # 블로그 변화 시 오류 방지
            return
                
    def GoDownloadURL():
        webbrowser.open(Update.update_url)

class UiFunction():
    def SetProgressLabelMessage(self, text, color='black'):
        self.progress_label.config(text = text, foreground=color)
        # self.progress_label.place(x=0, y=299, relx=0.5, anchor="s")
        
    def GetServer(self):
        return self.server_combobox.get()
        
    def GetUnionMin(self):
        return self.union_min_entry.get()
        
    def GetUnionMax(self):
        return self.union_max_entry.get()
    
    def EnableUi(self):
        self.server_combobox["state"] = "readonly"
        self.union_min_entry["state"] = "normal"
        self.union_max_entry["state"] = "normal"
        
    def DisableUi(self):
        self.server_combobox["state"] = "disabled"
        self.union_min_entry["state"] = "disabled"
        self.union_max_entry["state"] = "disabled"
    
    def SetRemainResetTime(self):
        text = f"Current Time in UTC: {datetime.utcnow().strftime('%#I:%M:%S %p')} ({UiFunction.time_until_next_4pm_utc()} left)"
        self.reset_remain_label.config(text = text)
        self.reset_remain_label.place(x=0, y=255, relx=0.5, anchor="s")

    def time_until_next_4pm_utc():
        # 현재 시간을 UTC로 가져오기
        now = datetime.now(timezone.utc)
        # 오늘 오후 4시(UTC) 구하기
        today_4pm = now.replace(hour=16, minute=0, second=0, microsecond=0)

        if now < today_4pm:
            # 현재 시간이 오후 4시 이전이라면
            time_difference = today_4pm - now
        else:
            # 현재 시간이 오후 4시 이후라면 다음 날 오후 4시 구하기
            tomorrow_4pm = today_4pm + timedelta(days=1)
            time_difference = tomorrow_4pm - now

        # 시간, 분, 초로 분리
        hours, remainder = divmod(time_difference.seconds, 3600)
        minutes, seconds = divmod(remainder, 60)

        if hours > 0:
            return f"{hours}h {minutes}m {seconds}s"
        elif minutes > 0:
            return f"{minutes}m {seconds}s"
        else:
            return f"{seconds}s"

class Ui(UiFunction):
    def __init__(self):
        self.win = Tk()
        self.win.title(f'I Will Find your Main character')
        self.win.iconbitmap(resource_path("img/app.ico"))
        self.win.geometry('330x345')
        # self.win.option_add('*Font', '맑은고딕 10')
        self.win.resizable(False, False)
        
        # Default Ui
        Ui.MenuBar(self)
        Ui.MainUi(self)
        
        # Check Update
        Update.CheckUpdate()



    def GetTime_Thread(self):
        t2=threading.Thread(target=Crawlling.GetTime_Thread)
        t2.setDaemon(True)
        t2.deamon = True
        t2.start()

    def MenuBar(self):
        def GoToMyGithub():
            webbrowser.open("https://github.com/nerious2/Maplestory-Character-Tracer-GMS")
        self.menubar = Menu(self.win)
        self.menu_1 = Menu(self.menubar, tearoff=0)
        self.menu_1.add_command(label="Github", command = GoToMyGithub)
        self.menubar.add_cascade(label="Option", menu=self.menu_1)
        self.win.config(menu=self.menubar)

    def MainUi(self):       
        # Main Image
        self.label_image = Label(self.win)
        self.main_image = ImageTk.PhotoImage(file = resource_path("img/title.jpg"))
        self.label_image = Label(self.win, image = self.main_image)
        # self.label_image.pack(side = "top")
        self.label_image.place(x=0, y=-5, relx=0.5, anchor="n")


        self.reset_remain_label = Label(self.win, text = '')
        self.reset_remain_label.place(x=0, y=235, relx=0.5, anchor="s")

        # Server UI
        self.server_label = Label(self.win, text = '[Server]')

        self.server_list =['Kronos', 'Hyperion', 'Scania', 'Bera', 'Aurora', 
                      'Elysium', 'Solis', 'Luna']


        self.server_combobox = ttk.Combobox(self.win, 
                                       width = 11, 
                                       values = self.server_list, 
                                       state="readonly")
        self.server_combobox.set("Kronos")
        
        self.server_label.place(x = 55 , y = 135)
        self.server_combobox.place(x = 160, y = 135) 
        
        # Union Range Ui
        self.union_label = Label(self.win, text = '[Legion Range]')
        self.union_min_entry = Entry(self.win, width = 5)
        self.union_range_label = Label(self.win, text = '-')
        self.union_max_entry = Entry(self.win, width = 5)
        self.union_placeholder_label = Label(self.win, text = 'low - high', font = tkinter.font.Font(size = 8))
        
        self.union_label.place(x = 30, y = 165)
        self.union_min_entry.place(x = 160, y = 165)
        self.union_range_label.place(x = 202, y = 165)
        self.union_max_entry.place(x = 220, y = 165)
        self.union_placeholder_label.place(x = 180, y = 185)
        
        # Progress Ui
        self.progress_label = Label(self.win, text = '', font = tkinter.font.Font(size = 8))
        self.progress_label.place(x=0, y=319, relx=0.5, anchor="s")

        # Legion Reset time text Ui
               
        self.reset_time_label = Label(self.win, text = 'Daily Update: Every Day at 4:00 PM UTC ')
        self.reset_time_label.place(x=0, y=232, relx=0.5, anchor="s")


        
        # Activate Button
        self.activate_button = Button(self.win, text = "Start", width = 25, height = 2, command = Crawlling.ValidateCrawlling_Thread)
        self.activate_button.place(x = 75, y = 260)
            
GUI = Ui()
GUI.GetTime_Thread()
GUI.win.mainloop()

- The problem of Magician (Fire, Posion), Magician (Ice, Lightning) being handled abnormally
- Add character image load
- Display character level


C:\Users\hrlee\AppData\Local\Temp\ipykernel_53588\3032612645.py:101: DeprecationWarning: setDaemon() is deprecated, set the daemon attribute instead
  t2.setDaemon(True)
C:\Users\hrlee\AppData\Local\Temp\ipykernel_53588\3280226421.py:178: DeprecationWarning: setDaemon() is deprecated, set the daemon attribute instead
  t1.setDaemon(True)


GetLegionJson: {'totalCount': 218944, 'ranks': [{'characterID': 0, 'characterName': 'Selenik', 'exp': 302704547607885, 'gap': 0, 'jobDetail': 12, 'jobID': 33, 'level': 291, 'rank': 1, 'startRank': 0, 'worldID': 45, 'characterImgURL': 'https://msavatar1.nexon.net/Character/CHAFPOOGHMPPGPIHIIOONNCGKGOIFEDMLJLBGLMBLEGJLACDCEDADDFJDPIFLOGGKHCFMDBBBHEOPOMBLPCMAOOMKMLLAGINPIMPKJCLEGKFHAAKNDNAGCLNKCPINCPNEDAIIOGLHNCKPCIGAOCJINBPCIAHKBCKFADJCCECJKAFKIKNBGALNGENMBJKGMKFEKKEPDMCLMNPAGEEKHOHFPBPABPBHGCNNDDMMMPOMHNLOAEENKBKLDEIBKDLLJME.png', 'worldName': 'Kronos', 'isSearchTarget': False, 'legionLevel': 10839, 'raidPower': 1379107116, 'tierName': '', 'score': 0}, {'characterID': 0, 'characterName': 'BSeductress', 'exp': 33207978963429, 'gap': 0, 'jobDetail': 12, 'jobID': 207, 'level': 283, 'rank': 2, 'startRank': 0, 'worldID': 45, 'characterImgURL': 'https://msavatar1.nexon.net/Character/IDBFJNDGCEGNAGPJMPKBEOGHBGLHGCNNOCIMBNHLPPILCILMFCJAAHCKGPAPGJKAEPNDPCIBKCECCOFCIFFCDKONMJJFKONLGEDJAHPBFAOFOHK